In [1]:
from sklearn.cluster import KMeans
import pandas as pd
import numpy as np
import warnings
from scipy import stats
from scipy.stats import percentileofscore
from IPython.utils import io
import math

warnings.filterwarnings('ignore')
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

#pd.set_option("display.precision", 10)

stars_dir = '~/GitHub/stars-data-builder/'


# Validate what-if function

The CMS stars app replicates the methodology of the hospital overall quality star rating system. This jupyter notebook validates that replicated methodology produces the same (or highly similar) results as the SAS source code of the overall star rating system.


In [2]:

# This function is currently setup for 2023 and 2024 predictions (i.e., includes OP_3B and OP_2). 
# Predictions for 2025 would exclude OP_3B and OP_2. 

# Note: OP_2 was included in the methodologies for 2023 and 2024, but was excluded due to 
# too few hospitals reporting it


def run_whatif(raw_data):
    
    def kmeans_clustering(df, n_clusters=5, col='summary_score'):
        
        tol = 0.00001
        rstate = 33
        # Step 1: Initial Data Preparation - Determine quintile medians as initial seeds
        quintiles = np.percentile(df[col].dropna(),
                                  [20.0, 40.0, 60.0, 80.0],
                                  method='interpolated_inverted_cdf', # this is good
                                  #method='linear',
                                 )
        
        df['grp'] = pd.cut(df[col], bins=[-np.inf] + quintiles.tolist() + [np.inf], labels=False) + 1
    
        # Step 2: Initial K-Means Clustering - Compute median for initial seeds
        initial_seeds = df.groupby('grp')[col].median().dropna().values.reshape(-1, 1)
    
        kmeans_initial = KMeans(n_clusters=len(initial_seeds), 
                                init=initial_seeds, 
                                n_init=100, 
                                max_iter=1000, 
                                random_state=rstate,
                                tol=tol,
                                #algorithm='full',
                               )
        
        kmeans_initial.fit(df[[col]].dropna())
    
        # Use cluster centers from initial k-means as seeds for the main clustering
        main_seeds = kmeans_initial.cluster_centers_
    
        # Step 3: Second K-Means Clustering - Main clustering with refined seeds
        kmeans_main = KMeans(n_clusters=n_clusters, 
                             init=main_seeds, 
                             n_init=100, 
                             max_iter=1000, 
                             random_state=rstate,
                             tol=tol,
                             #algorithm='full',
                            )
        df['cluster'] = kmeans_main.fit_predict(df[[col]].dropna())
    
        # Step 4: Cluster Ordering and Labeling - Order clusters and assign 'star' ratings
        cluster_means = df.groupby('cluster')[col].mean().sort_values().index
        cluster_mapping = {old: new for new, old in enumerate(cluster_means, 1)}
    
        df['star'] = df['cluster'].map(cluster_mapping)
        df.drop('cluster', axis=1, inplace=True)
    
        return df

    measures = ['MORT_30_AMI', 'MORT_30_CABG', 'MORT_30_COPD', 'MORT_30_HF',
                'MORT_30_PN', 'MORT_30_STK', 'PSI_4_SURG_COMP', 'COMP_HIP_KNEE',
                'HAI_1', 'HAI_2', 'HAI_3', 'HAI_4', 'HAI_5', 'HAI_6', 
                'PSI_90_SAFETY', 'EDAC_30_AMI', 'EDAC_30_HF',
                'EDAC_30_PN', 'OP_32', 'READM_30_CABG', 'READM_30_COPD',
                'READM_30_HIP_KNEE', 'READM_30_HOSP_WIDE', 'OP_35_ADM', 
                'OP_35_ED', 'OP_36', 'H_COMP_1_STAR_RATING', 'H_COMP_2_STAR_RATING', 
                'H_COMP_3_STAR_RATING', 'H_COMP_5_STAR_RATING', 
                'H_COMP_6_STAR_RATING', 'H_COMP_7_STAR_RATING', 
                'H_GLOB_STAR_RATING', 'H_INDI_STAR_RATING', 'HCP_COVID_19', 
                'IMM_3', 'OP_10', 'OP_13', 'OP_18B', 'OP_2', 'OP_22',
                'OP_23', 'OP_29', 'OP_3B', 'OP_8', 'PC_01', 'SEP_1',
               ]
    
    print(len(measures), 'measures')
    prvdrs = raw_data['PROVIDER_ID']
    raw_data = raw_data.filter(items=measures)
    filtered_data = raw_data.dropna(axis=1, thresh=101)
    filtered_measures = list(filtered_data)
    
    excluded = [item for item in measures if item not in filtered_measures]
    print('Excluded measure(s):', excluded)
    filtered_data.dropna(how='all', subset=filtered_measures, axis=0, inplace=True)
    
    print('Shape of filtered dataframe:', filtered_data.shape)
    print('Final no. of measures:', filtered_data.shape[1])
    filtered_data['PROVIDER_ID'] = prvdrs
    filtered_data = filtered_data[filtered_data.columns[-1:].tolist() + filtered_data.columns[:-1].tolist()]

    ddof = 1
    zscore_df = filtered_data.copy(deep=True)
    for m in measures:
        if m in excluded:
            continue
            
        zscore_df[m] = stats.zscore(zscore_df[m], ddof=ddof, nan_policy='omit')
        
    rev_measures = ['MORT_30_AMI', 'MORT_30_CABG', 'MORT_30_COPD', 'MORT_30_HF',
                    'MORT_30_PN', 'MORT_30_STK', 'PSI_4_SURG_COMP', 'COMP_HIP_KNEE', 
                    'HAI_1', 'HAI_2', 'HAI_3', 'HAI_4', 'HAI_5', 'HAI_6',
                    'PSI_90_SAFETY', 'EDAC_30_AMI', 'EDAC_30_HF', 'EDAC_30_PN',
                    'OP_32', 'READM_30_CABG', 'READM_30_COPD', 
                    'READM_30_HIP_KNEE', 'READM_30_HOSP_WIDE',
                    'OP_35_ADM', 'OP_35_ED', 'OP_36', 'OP_22',
                    'PC_01', 'OP_3B', 'OP_18B', 'OP_8', 
                    'OP_10','OP_13',
                   ]
    for m in rev_measures:
        zscore_df[m] = -1*zscore_df[m]
        zscore_df[m] = zscore_df[m]
        
    final_df = pd.DataFrame(columns=['PROVIDER_ID'])
    final_df['PROVIDER_ID'] = zscore_df['PROVIDER_ID']
    
    # 7 Mortality measures
    mort_measures = ['MORT_30_AMI', 'MORT_30_CABG', 'MORT_30_COPD', 'MORT_30_HF', 
                     'MORT_30_PN', 'MORT_30_STK', 'PSI_4_SURG_COMP']
    final_df['Std_Outcomes_Mortality_score'] = stats.zscore(zscore_df[mort_measures].mean(axis=1), ddof=ddof, nan_policy='omit')
    final_df['Outcomes_Mortality_cnt'] = zscore_df[mort_measures].apply(lambda row: row.notna().sum(), axis=1)
    
    
    # 11 Readmission measures
    readm_measures = ['EDAC_30_AMI', 'EDAC_30_HF', 'EDAC_30_PN', 'OP_32',
                      'READM_30_CABG', 'READM_30_COPD', 'READM_30_HIP_KNEE', 
                      'READM_30_HOSP_WIDE', 'OP_35_ADM', 'OP_35_ED', 'OP_36']
    final_df['Std_Outcomes_Readmission_score'] = stats.zscore(zscore_df[readm_measures].mean(axis=1), ddof=ddof, nan_policy='omit')
    final_df['Outcomes_Readmission_cnt'] = zscore_df[readm_measures].apply(lambda row: row.notna().sum(), axis=1)
    
    
    # 8 SAFETY measures
    safety_measures = ['COMP_HIP_KNEE',  'HAI_1', 'HAI_2', 'HAI_3', 'HAI_4', 
                       'HAI_5', 'HAI_6', 'PSI_90_SAFETY']
    final_df['Std_Outcomes_Safety_score'] = stats.zscore(zscore_df[safety_measures].mean(axis=1), ddof=ddof, nan_policy='omit')
    final_df['Outcomes_safety_cnt'] = zscore_df[safety_measures].apply(lambda row: row.notna().sum(), axis=1)
    
    
    # 8 Patient experience measures
    patexp_measures = ['H_COMP_1_STAR_RATING', 'H_COMP_2_STAR_RATING', 
                       'H_COMP_3_STAR_RATING', 'H_COMP_5_STAR_RATING', 
                       'H_COMP_6_STAR_RATING', 'H_COMP_7_STAR_RATING', 
                       'H_GLOB_STAR_RATING', 'H_INDI_STAR_RATING']
    final_df['Std_PatientExp_score'] = stats.zscore(zscore_df[patexp_measures].mean(axis=1), ddof=ddof, nan_policy='omit')
    final_df['Patient_Experience_cnt'] = zscore_df[patexp_measures].apply(lambda row: row.notna().sum(), axis=1)
    
    
    # 13 Process measures
    proc_measures = ['HCP_COVID_19', 'IMM_3', 'OP_10', 'OP_13', 'OP_18B', 
                     #'OP_2', 
                     'OP_22', 'OP_23', 'OP_29', 'OP_3B',  
                     'OP_8', 'PC_01', 'SEP_1']
    final_df['Std_Process_score'] = stats.zscore(zscore_df[proc_measures].mean(axis=1), ddof=ddof, nan_policy='omit')
    final_df['Process_cnt'] = zscore_df[proc_measures].apply(lambda row: row.notna().sum(), axis=1)
    
    
    mort_cnts = final_df['Outcomes_Mortality_cnt'].tolist()
    safe_cnts = final_df['Outcomes_safety_cnt'].tolist()
    read_cnts = final_df['Outcomes_Readmission_cnt'].tolist()
    pate_cnts = final_df['Patient_Experience_cnt'].tolist()
    proc_cnts = final_df['Process_cnt'].tolist()
    
    tot_cnts = []
    msg_cnts = []
    grp_cnts = []
    for i, m in enumerate(mort_cnts):
        ct = 0
        ct2 = 0
        if m > 2:
            ct += 1
            ct2 +=1
        if safe_cnts[i] > 2:
            ct += 1
            ct2 += 1
        if read_cnts[i] > 2:
            ct += 1
        if pate_cnts[i] > 2:
            ct += 1
        if proc_cnts[i] > 2:
            ct += 1
            
        tot_cnts.append(ct)
        msg_cnts.append(ct2)
        
        if ct == 3:
            grp_cnts.append('1) # of groups=3')
        elif ct == 4:
            grp_cnts.append('2) # of groups=4')
        elif ct == 5:
            grp_cnts.append('3) # of groups=5')
        else:
            grp_cnts.append('Not grouped')
    
    final_df['Total_measure_group_cnt'] = tot_cnts
    final_df['MortSafe_Group_cnt'] = msg_cnts
    final_df['cnt_grp'] = grp_cnts
    
    
    # Add standard group measure weights
    final_df['std_weight_PatientExperience'] = 0.22
    final_df['std_weight_Readmission'] = 0.22
    final_df['std_weight_Mortality'] = 0.22
    final_df['std_weight_safety'] = 0.22
    final_df['std_weight_Process'] = 0.12
    
    # Standard weights and their corresponding score columns
    weights_info = {
        'Std_PatientExp_score': ('weight_PatientExperience', 0.22),
        'Std_Outcomes_Readmission_score': ('weight_Outcomes_Readmission', 0.22),
        'Std_Outcomes_Mortality_score': ('weight_Outcomes_Mortality', 0.22),
        'Std_Outcomes_Safety_score': ('weight_Outcomes_Safety', 0.22),
        'Std_Process_score': ('weight_Process', 0.12)
    }
    
    # Function to adjust weights
    def adjust_weights(row):
        # Extract scores and check for NaN
        scores = {score: row[score] for score in weights_info.keys()}
        non_missing_scores = {k: v for k, v in scores.items() if pd.notnull(v)}
        
        # Sum of weights for non-missing scores
        sum_weights = sum(weights_info[k][1] for k in non_missing_scores.keys())
        
        # Assign adjusted weights or 0 if score is missing
        for score, (new_col, weight) in weights_info.items():
            if score in non_missing_scores:
                row[new_col] = weight / sum_weights
            else:
                row[new_col] = 0  # Set weight to 0 if score is missing
        
        return row
    
    # Apply the function to each row
    final_df = final_df.apply(adjust_weights, axis=1)
    
    # Define score columns and their corresponding adjusted weight columns
    score_columns = [
        'Std_PatientExp_score',
        'Std_Outcomes_Readmission_score',
        'Std_Outcomes_Mortality_score',
        'Std_Outcomes_Safety_score',
        'Std_Process_score'
    ]
    weight_columns = [
        'weight_PatientExperience',
        'weight_Outcomes_Readmission',
        'weight_Outcomes_Mortality',
        'weight_Outcomes_Safety',
        'weight_Process'
    ]
    
    # Calculate weighted average for each row
    final_df['summary_score'] = final_df.apply(lambda row: sum(row[score] * row[weight] for score, weight in zip(score_columns, weight_columns) if pd.notnull(row[score])), axis=1)
    
    final_df = final_df[final_df['cnt_grp'] != 'Not grouped']
    final_df = final_df[final_df['MortSafe_Group_cnt'] > 0]
    final_df['report_indicator'] = 1
    
    dfg3 = final_df[final_df['cnt_grp'] == '1) # of groups=3']
    dfg3 = kmeans_clustering(dfg3)
    dfg4 = final_df[final_df['cnt_grp'] == '2) # of groups=4']
    dfg4 = kmeans_clustering(dfg4)
    dfg5 = final_df[final_df['cnt_grp'] == '3) # of groups=5']
    dfg5 = kmeans_clustering(dfg5)
    
    complete_df = pd.concat([dfg3, dfg4, dfg5])
    
    complete_df.drop(labels=['grp'], axis=1, inplace=True)
    return complete_df


In [3]:
def compare_results(osr_input_df, osr_results_df):

    whatif_df = run_whatif(osr_input_df)

    whatif_df['star'] = whatif_df['star'].astype(float) 
    osr_results_df = osr_results_df[osr_results_df['star'].isin([1,2,3,4,5])]

    print('osr_results_df.shape:', osr_results_df.shape)
    print('whatif_df.shape:', whatif_df.shape)

    print(osr_results_df['star'].unique().tolist())
    print(whatif_df['star'].unique().tolist())

    osr_results_df.sort_values(by=['PROVIDER_ID'], ascending=True, inplace=True)
    whatif_df.sort_values(by=['PROVIDER_ID'], ascending=True, inplace=True)

    osr_prvdrs = osr_results_df['PROVIDER_ID'].tolist()
    whatif_prvdrs = whatif_df['PROVIDER_ID'].tolist()

    for i, p1 in enumerate(osr_prvdrs):
        p2 = whatif_prvdrs[i]

        if p1 != p2:
            print('Error:', p1, p2)

    
    cols = ['Std_Outcomes_Mortality_score', 'Std_Outcomes_Readmission_score',
            'Std_Outcomes_Safety_score', 'Std_PatientExp_score',
            'Std_Process_score', 'summary_score']
    for col in cols:

        ct = 0
        ls1 = whatif_df[col].tolist()
        ls2 = osr_results_df[col].tolist()
        
        pairs = [(a, b) for a, b in zip(ls1, ls2) if not (math.isnan(a) or math.isnan(b))]

        abs_diffs = [abs(a - b) for a, b in pairs]

        avg_abs_diff = sum(abs_diffs) / len(abs_diffs)

        print(col)
        #print("Average Abs Diff:", round(avg_abs_diff, 6))
        #print("Max Abs Diff:", round(np.nanmax(abs_diffs), 6), '\n')
        print("Average Abs Diff:", avg_abs_diff)
        print("Max Abs Diff:", np.nanmax(abs_diffs), '\n')
            
    
    cols = ['Outcomes_Mortality_cnt', 'Outcomes_safety_cnt', 'Outcomes_Readmission_cnt', 
            'Patient_Experience_cnt', 'Process_cnt', 'Total_measure_group_cnt',
            'MortSafe_Group_cnt', 'report_indicator', 'cnt_grp', 'star']
    for col in cols:

        ct = 0
        ls1 = whatif_df[col].tolist()
        ls2 = osr_results_df[col].tolist()

        for i, v1 in enumerate(ls1):
            v2 = ls2[i]
            if v1 != v2:
                ct += 1
                if np.abs(v1 - v2) > 1:
                    print('Error:', v1, v2)

        print(col, ct, 'incorrect')

        print(100 * (1 - ct/whatif_df.shape[0]), '% correct\n')
        if col == 'star':
            print(whatif_df.shape[0])
    return whatif_df


# 2023

In [4]:
osr_results_df = pd.read_csv(stars_dir + '2023/2023-07 Stars Release/SAS_CSV_output/CMS_Stars_Jul_2023.csv')

with io.capture_output() as captured: 
    osr_input_df = pd.read_sas(stars_dir + '2023/2023-07 Stars Release/alldata_2023jul.sas7bdat')

osr_input_df = osr_input_df.applymap(lambda x: x.decode() if isinstance(x, bytes) else x)

whatif_df = compare_results(osr_input_df, osr_results_df)


47 measures
Excluded measure(s): ['OP_2']
Shape of filtered dataframe: (4654, 46)
Final no. of measures: 46
osr_results_df.shape: (3076, 27)
whatif_df.shape: (3076, 27)
[3.0, 2.0, 1.0, 4.0, 5.0]
[2.0, 5.0, 3.0, 4.0, 1.0]
Std_Outcomes_Mortality_score
Average Abs Diff: 1.2470674163755724e-10
Max Abs Diff: 4.998536029532374e-10 

Std_Outcomes_Readmission_score
Average Abs Diff: 1.38777057588939e-10
Max Abs Diff: 4.997278146845474e-10 

Std_Outcomes_Safety_score
Average Abs Diff: 1.2063587429360548e-10
Max Abs Diff: 8.922462768623518e-10 

Std_PatientExp_score
Average Abs Diff: 1.4660704906422648e-10
Max Abs Diff: 4.999721192611162e-10 

Std_Process_score
Average Abs Diff: 1.4613296433904228e-10
Max Abs Diff: 4.483208471128819e-09 

summary_score
Average Abs Diff: 1.4451587562512478e-10
Max Abs Diff: 4.99769434170183e-10 

Outcomes_Mortality_cnt 0 incorrect
100.0 % correct

Outcomes_safety_cnt 0 incorrect
100.0 % correct

Outcomes_Readmission_cnt 0 incorrect
100.0 % correct

Patient_Experi

In [5]:
osr_results_df = osr_results_df[osr_results_df['star'].isin([1,2,3,4,5])]
print(osr_results_df.shape)
osr_results_df.head()

(3076, 27)


PROVIDER_ID  Std_Outcomes_Mortality_score  Std_Outcomes_Readmission_score  \
0      010001                     -0.647058                        0.284081   
1      010005                     -1.564103                        0.560369   
2      010006                     -1.694318                       -0.554988   
3      010007                     -2.407150                       -0.488553   
5      010011                     -0.517349                       -0.624302   

   Std_Outcomes_Safety_score  Std_PatientExp_score  Std_Process_score  \
0                   0.312074             -0.127836          -1.024044   
1                  -0.237844             -0.166838          -0.302742   
2                  -0.089526             -1.241108          -0.179350   
3                   0.022657              0.993806          -0.659760   
5                   0.428770              0.134223          -2.385055   

   std_weight_PatientExperience  std_weight_Readmission  std_weight_Mortality  \
0                          0.22                    0.22                  0.22   
1                          0.22                    0.22                  0.22   
2                          0.22                    0.22                  0.22   
3                          0.22                    0.22                  0.22   
5                          0.22                    0.22                  0.22   

   std_weight_safety  std_weight_Process  weight_PatientExperience  \
0               0.22                0.12                      0.22   
1               0.22                0.12                      0.22   
2               0.22                0.12                      0.22   
3               0.22                0.12                      0.22   
5               0.22                0.12                      0.22   

   weight_Outcomes_Readmission  weight_Outcomes_Mortality  \
0                         0.22                       0.22   
1                         0.22                       0.22   
2                         0.22                       0.22   
3                         0.22                       0.22   
5                         0.22                       0.22   

   weight_Outcomes_Safety  weight_Process  summary_score  \
0                    0.22            0.12      -0.162208   
1                    0.22            0.12      -0.346181   
2                    0.22            0.12      -0.809109   
3                    0.22            0.12      -0.492604   
5                    0.22            0.12      -0.413511   

   Outcomes_Mortality_cnt  Outcomes_safety_cnt  Outcomes_Readmission_cnt  \
0                       7                    8                        11   
1                       6                    7                        10   
2                       7                    7                         9   
3                       3                    2                         6   
5                       7                    7                         9   

   Patient_Experience_cnt  Process_cnt  Total_measure_group_cnt  \
0                       8           10                        5   
1                       8           11                        5   
2                       8           11                        5   
3                       8            7                        4   
5                       8            8                        5   

   MortSafe_Group_cnt  report_indicator           cnt_grp  star  
0                   2                 1  3) # of groups=5   3.0  
1                   2                 1  3) # of groups=5   2.0  
2                   2                 1  3) # of groups=5   1.0  
3                   1                 1  2) # of groups=4   2.0  
5                   2                 1  3) # of groups=5   2.0

In [6]:
whatif_df = whatif_df.filter(items=list(osr_results_df))
print(whatif_df.shape)
whatif_df.head()

(3076, 27)


PROVIDER_ID  Std_Outcomes_Mortality_score  Std_Outcomes_Readmission_score  \
0      010001                     -0.647058                        0.284081   
1      010005                     -1.564103                        0.560369   
2      010006                     -1.694318                       -0.554988   
3      010007                     -2.407150                       -0.488553   
5      010011                     -0.517349                       -0.624302   

   Std_Outcomes_Safety_score  Std_PatientExp_score  Std_Process_score  \
0                   0.312074             -0.127836          -1.024044   
1                  -0.237844             -0.166838          -0.302742   
2                  -0.089526             -1.241108          -0.179350   
3                   0.022657              0.993806          -0.659760   
5                   0.428770              0.134223          -2.385055   

   std_weight_PatientExperience  std_weight_Readmission  std_weight_Mortality  \
0                          0.22                    0.22                  0.22   
1                          0.22                    0.22                  0.22   
2                          0.22                    0.22                  0.22   
3                          0.22                    0.22                  0.22   
5                          0.22                    0.22                  0.22   

   std_weight_safety  std_weight_Process  weight_PatientExperience  \
0               0.22                0.12                      0.22   
1               0.22                0.12                      0.22   
2               0.22                0.12                      0.22   
3               0.22                0.12                      0.22   
5               0.22                0.12                      0.22   

   weight_Outcomes_Readmission  weight_Outcomes_Mortality  \
0                         0.22                       0.22   
1                         0.22                       0.22   
2                         0.22                       0.22   
3                         0.22                       0.22   
5                         0.22                       0.22   

   weight_Outcomes_Safety  weight_Process  summary_score  \
0                    0.22            0.12      -0.162208   
1                    0.22            0.12      -0.346181   
2                    0.22            0.12      -0.809109   
3                    0.22            0.12      -0.492604   
5                    0.22            0.12      -0.413511   

   Outcomes_Mortality_cnt  Outcomes_safety_cnt  Outcomes_Readmission_cnt  \
0                       7                    8                        11   
1                       6                    7                        10   
2                       7                    7                         9   
3                       3                    2                         6   
5                       7                    7                         9   

   Patient_Experience_cnt  Process_cnt  Total_measure_group_cnt  \
0                       8           10                        5   
1                       8           11                        5   
2                       8           11                        5   
3                       8            7                        4   
5                       8            8                        5   

   MortSafe_Group_cnt  report_indicator           cnt_grp  star  
0                   2                 1  3) # of groups=5   3.0  
1                   2                 1  3) # of groups=5   2.0  
2                   2                 1  3) # of groups=5   1.0  
3                   1                 1  2) # of groups=4   2.0  
5                   2                 1  3) # of groups=5   2.0

# 2024

In [7]:
osr_results_df = pd.read_csv(stars_dir + '2024/2024-07 Stars Release/SAS_CSV_output/CMS_Stars_Jul_2024.csv')

with io.capture_output() as captured: 
    osr_input_df = pd.read_sas(stars_dir + '2024/2024-07 Stars Release/alldata_2024jul.sas7bdat')

osr_input_df = osr_input_df.applymap(lambda x: x.decode() if isinstance(x, bytes) else x)

compare_results(osr_input_df, osr_results_df)



47 measures
Excluded measure(s): ['OP_2']
Shape of filtered dataframe: (4626, 46)
Final no. of measures: 46
osr_results_df.shape: (2847, 27)
whatif_df.shape: (2847, 27)
[3.0, 2.0, 1.0, 4.0, 5.0]
[2.0, 4.0, 3.0, 5.0, 1.0]
Std_Outcomes_Mortality_score
Average Abs Diff: 1.2372953060012173e-10
Max Abs Diff: 4.998885749785131e-10 

Std_Outcomes_Readmission_score
Average Abs Diff: 1.3882012689449318e-10
Max Abs Diff: 4.999928249205254e-10 

Std_Outcomes_Safety_score
Average Abs Diff: 1.2241131170952426e-10
Max Abs Diff: 4.176067491812319e-09 

Std_PatientExp_score
Average Abs Diff: 1.5162458463564611e-10
Max Abs Diff: 4.997191549449553e-10 

Std_Process_score
Average Abs Diff: 1.4981568396662414e-10
Max Abs Diff: 4.993472302317059e-10 

summary_score
Average Abs Diff: 1.4254673671504467e-10
Max Abs Diff: 4.988656154836235e-10 

Outcomes_Mortality_cnt 0 incorrect
100.0 % correct

Outcomes_safety_cnt 0 incorrect
100.0 % correct

Outcomes_Readmission_cnt 0 incorrect
100.0 % correct

Patient_Exp

PROVIDER_ID  Std_Outcomes_Mortality_score  Outcomes_Mortality_cnt  \
0         010001                  7.071064e-03                       7   
1         010005                 -1.440587e+00                       6   
2         010006                 -1.462748e+00                       7   
3         010007                 -3.527615e+00                       3   
5         010011                 -4.767204e-01                       7   
6         010012                 -1.532571e+00                       3   
7         010016                  5.364458e-01                       7   
9         010019                 -2.238530e+00                       4   
10        010021                 -4.143043e-01                       3   
12        010023                 -9.024098e-01                       7   
13        010024                 -7.581164e-01                       7   
14        010029                 -1.141460e+00                       7   
15        010033                  2.777639e-02                       7   
17        010035                 -4.198977e-01                       6   
18        010036                 -5.903493e-01                       4   
19        010039                 -1.142166e+00                       7   
20        010040                  3.064030e-02                       7   
22        010045                  4.648595e-01                       3   
23        010046                  2.431161e-01                       6   
24        010049                 -1.787337e+00                       4   
27        010055                 -2.085426e+00                       7   
28        010056                 -1.715550e-01                       7   
31        010061                 -4.732173e-01                       3   
33        010065                 -4.300935e-01                       3   
36        010078                  8.164988e-02                       6   
37        010079                 -9.388313e-01                       4   
38        010083                  9.346037e-02                       6   
39        010085                 -1.331720e-01                       6   
40        010086                 -1.369329e+00                       3   
41        010087                  2.277300e-01                       4   
42        010089                 -1.731022e-02                       4   
43        010090                 -1.270591e+00                       7   
45        010092                 -8.400975e-01                       7   
49        010100                 -5.371247e-01                       7   
52        010103                 -4.028273e-01                       7   
53        010104                 -1.156190e+00                       7   
54        010108                  2.980138e-01                       4   
57        010113                 -1.037172e+00                       7   
58        010114                  4.520701e-01                       3   
59        010118                 -3.402028e-01                       4   
61        010125                  8.546681e-01                       3   
65        010130                 -1.013040e+00                       4   
66        010131                 -4.522214e-01                       6   
68        010139                 -5.909058e-01                       7   
69        010144                 -2.897171e-01                       7   
70        010148                 -1.025061e+00                       3   
71        010149                 -1.198742e+00                       4   
72        01014F                  2.167162e+00                       5   
76        010164                 -9.080228e-01                       3   
77        010168                           NaN                       0   
82        01019F                  1.806357e+00                       3   
89        020001                 -1.947749e-01                       7   
90        020006                 -1.581950e+00                       6   
91       